In [1]:
!pip install --quiet img2vec_pytorch
print('pip install img2vec complete.')

pip install img2vec complete.


Let's use img2vec to encode all of our images as vectors. Loading all the data takes about 20 minutes.

In [2]:
import base64
import pandas as pd
from arrow import now
from glob import glob
from img2vec_pytorch import Img2Vec
from io import BytesIO
from os.path import basename
from PIL import Image

# we're going to use the updated dataset
GLOB = '/kaggle/input/arabic-characters/Arabic Character Dataset/Train Arabic'
SIZE = 512
STOP = 10000
THUMBNAIL_SIZE = (128, 128)


def embed(model, filename: str):
    with Image.open(fp=filename, mode='r') as image:
        return model.get_vec(image.convert('RGB'), tensor=True).numpy().reshape(SIZE,)


# https://stackoverflow.com/a/952952
def flatten(arg):
    return [x for xs in arg for x in xs]

def png(filename: str) -> str:
    with Image.open(fp=filename, mode='r') as image:
        buffer = BytesIO()
        # our images are pretty big; let's shrink the hover images to thumbnail size
        image.resize(size=THUMBNAIL_SIZE).save(buffer, format='png')
        return 'data:image/png;base64,' + base64.b64encode(buffer.getvalue()).decode()

def get_picture_from_glob(arg: str, tag: str, stop: int) -> list:
    time_get = now()
    result = [pd.Series(data=[tag, basename(input_file), embed(model=model, filename=input_file), png(filename=input_file), ],
                        index=['tag', 'name', 'value', 'image'])
        for index, input_file in enumerate(glob(pathname=arg)) if index < stop]
    print('encoded {} rows of {}  in {}'.format(len(result), tag, now() - time_get))
    return result

time_start = now()
model = Img2Vec(cuda=False, model='resnet-18')
data_dict = {basename(folder) : folder + '/*.*' for folder in glob(GLOB + '/*')}
df = pd.DataFrame(data=flatten(arg=[get_picture_from_glob(arg=value, tag=key, stop=STOP) for key, value in data_dict.items()]))
print('done in {}'.format(now() - time_start))

/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet18-f37072fd.pth" to /root/.cache/torch/hub/checkpoints/resnet18-f37072fd.pth
100%|██████████| 44.7M/44.7M [00:00<00:00, 127MB/s]


encoded 480 rows of 7  in 0:00:27.586245
encoded 480 rows of 17  in 0:00:27.235612
encoded 480 rows of 19  in 0:00:27.408283
encoded 480 rows of 22  in 0:00:26.455505
encoded 480 rows of 2  in 0:00:26.240510
encoded 480 rows of 23  in 0:00:25.854333
encoded 480 rows of 10  in 0:00:26.460010
encoded 480 rows of 5  in 0:00:25.542990
encoded 480 rows of 20  in 0:00:25.568365
encoded 480 rows of 27  in 0:00:26.001121
encoded 480 rows of 25  in 0:00:25.603763
encoded 480 rows of 8  in 0:00:24.961531
encoded 480 rows of 12  in 0:00:25.822406
encoded 480 rows of 18  in 0:00:25.949276
encoded 480 rows of 28  in 0:00:25.828790
encoded 480 rows of 16  in 0:00:26.921251
encoded 480 rows of 13  in 0:00:26.514567
encoded 480 rows of 26  in 0:00:26.655313
encoded 480 rows of 15  in 0:00:27.713495
encoded 480 rows of 3  in 0:00:27.704246
encoded 480 rows of 1  in 0:00:27.819676
encoded 480 rows of 14  in 0:00:26.840603
encoded 480 rows of 4  in 0:00:27.071339
encoded 480 rows of 9  in 0:00:27.561366


In [3]:
TEST = '/kaggle/input/arabic-characters/Arabic Character Dataset/Test Arabic'
time_start = now()
test_dict = {basename(folder) : folder + '/*.*' for folder in glob(TEST + '/*')}
test_df = pd.DataFrame(data=flatten(arg=[get_picture_from_glob(arg=value, tag=key, stop=STOP) for key, value in test_dict.items()]))
test_df.head()
print('done in {}'.format(now() - time_start))

encoded 120 rows of 7  in 0:00:06.651794
encoded 120 rows of 17  in 0:00:06.619084
encoded 120 rows of 19  in 0:00:07.196872
encoded 120 rows of 22  in 0:00:06.719746
encoded 120 rows of 2  in 0:00:06.731014
encoded 120 rows of 23  in 0:00:06.899300
encoded 120 rows of 10  in 0:00:07.129353
encoded 120 rows of 5  in 0:00:06.803379
encoded 120 rows of 20  in 0:00:06.725998
encoded 120 rows of 27  in 0:00:06.599149
encoded 120 rows of 25  in 0:00:06.632190
encoded 120 rows of 8  in 0:00:07.052960
encoded 120 rows of 12  in 0:00:06.692966
encoded 120 rows of 18  in 0:00:06.802703
encoded 120 rows of 28  in 0:00:06.798431
encoded 120 rows of 16  in 0:00:07.050843
encoded 120 rows of 13  in 0:00:07.600131
encoded 120 rows of 26  in 0:00:06.628061
encoded 120 rows of 15  in 0:00:06.728916
encoded 120 rows of 3  in 0:00:06.843480
encoded 120 rows of 1  in 0:00:07.270226
encoded 120 rows of 14  in 0:00:06.968783
encoded 120 rows of 4  in 0:00:06.790603
encoded 120 rows of 9  in 0:00:06.680117


In [4]:
from plotly import express
express.histogram(data_frame=df, x='tag')

Our classes are balanced. Let's use dimension reduction to visualize.

In [5]:
from arrow import now
from umap import UMAP

time_start = now()
umap = UMAP(random_state=2024, verbose=True, n_jobs=1, low_memory=False, n_epochs=201)
df[['x', 'y']] = umap.fit_transform(X=df['value'].apply(func=pd.Series))
print('done with UMAP in {}'.format(now() - time_start))

2024-03-21 18:33:58.862389: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-21 18:33:58.862576: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-21 18:33:59.010921: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


UMAP(low_memory=False, n_epochs=201, n_jobs=1, random_state=2024, verbose=True)
Thu Mar 21 18:34:11 2024 Construct fuzzy simplicial set
Thu Mar 21 18:34:11 2024 Finding Nearest Neighbors
Thu Mar 21 18:34:11 2024 Building RP forest with 11 trees
Thu Mar 21 18:34:17 2024 NN descent for 14 iterations
	 1  /  14
	 2  /  14
	 3  /  14
	 4  /  14
	 5  /  14
	 6  /  14
	Stopping threshold met -- exiting after 6 iterations
Thu Mar 21 18:34:35 2024 Finished Nearest Neighbor Search
Thu Mar 21 18:34:39 2024 Construct embedding


Epochs completed:   0%|            0/201 [00:00]

	completed  0  /  201 epochs
	completed  20  /  201 epochs
	completed  40  /  201 epochs
	completed  60  /  201 epochs
	completed  80  /  201 epochs
	completed  100  /  201 epochs
	completed  120  /  201 epochs
	completed  140  /  201 epochs
	completed  160  /  201 epochs
	completed  180  /  201 epochs
	completed  200  /  201 epochs
Thu Mar 21 18:34:50 2024 Finished embedding
done with UMAP in 0:00:40.311602


In [6]:
from bokeh.models import ColumnDataSource
from bokeh.models import HoverTool

from bokeh.plotting import figure
from bokeh.plotting import output_notebook
from bokeh.plotting import show
from bokeh.palettes import Turbo256
from bokeh.transform import linear_cmap

output_notebook()

datasource = ColumnDataSource(df.sample(n=2000, random_state=2024))
mapper = linear_cmap(field_name = 'tag', palette=Turbo256, low=1, high=27,)

plot_figure = figure(title='UMAP projection: Arabic characters', width=1000, height=800, tools=('pan, wheel_zoom, reset'))

plot_figure.add_tools(HoverTool(tooltips="""
<div>
    <div>
        <img src='@image' style='float: left; margin: 5px 5px 5px 5px'/>
    </div>
    <div>
        <span style='font-size: 16px; color: #224499'>tag:</span>
        <span style='font-size: 18px'>@tag</span>
    </div>
</div>
"""))

plot_figure.circle('x', 'y', source=datasource, line_alpha=0.6, fill_alpha=0.6, size=5, color=mapper)
show(plot_figure)

Loading BokehJS ...

This looks pretty good; we have clustering but not a lot of separation. Let's build a model.

In [7]:
import arrow
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

time_start = arrow.now()
model = LogisticRegression(max_iter=100000, tol=1e-7).fit(X=df['value'].apply(func=pd.Series), y=df['tag'])
print('model fit in {} iterations took {}'.format(model.n_iter_[0], arrow.now() - time_start))

print('accuracy: {:5.4f}'.format(accuracy_score(y_true=test_df['tag'], y_pred=model.predict(X=test_df['value'].apply(func=pd.Series)))))
print('model done in {}'.format(now() - time_start))

model fit in 2745 iterations took 0:03:45.119306
accuracy: 0.8557
model done in 0:03:45.574820


In [8]:
from sklearn.metrics import confusion_matrix

express.imshow(img=confusion_matrix(y_true=test_df['tag'], y_pred=model.predict(X=test_df['value'].apply(func=pd.Series))))